In [1]:
import pandas as pd
import numpy as np

## Read the CSV

In [2]:
# loading the dataset
df = pd.read_csv("resources/train_transformed_2.csv")
df

Survived  Pclass  Age  SibSp  Parch     Fare  Family_Size  Age*Class  \
0           0       3   22      1      0   7.2500            1         66   
1           1       1   38      1      0  71.2833            1         38   
2           1       3   26      0      0   7.9250            0         78   
3           1       1   35      1      0  53.1000            1         35   
4           0       3   35      0      0   8.0500            0        105   
..        ...     ...  ...    ...    ...      ...          ...        ...   
884         0       2   27      0      0  13.0000            0         54   
885         1       1   19      0      0  30.0000            0         19   
886         0       3   17      1      2  23.4500            3         51   
887         1       1   26      0      0  30.0000            0         26   
888         0       3   32      0      0   7.7500            0         96   

     Fare_Per_Person  Sex_female  ...  Title_Mrs  Deck_A  Deck_B  Deck_C  \
0            3.62500           0  ...          0       0       0       0   
1           35.64165           1  ...          1       0       0       1   
2            7.92500           1  ...          0       0       0       0   
3           26.55000           1  ...          1       0       0       1   
4            8.05000           0  ...          0       0       0       0   
..               ...         ...  ...        ...     ...     ...     ...   
884         13.00000           0  ...          0       0       0       0   
885         30.00000           1  ...          0       0       1       0   
886          5.86250           1  ...          0       0       0       0   
887         30.00000           0  ...          0       0       0       1   
888          7.75000           0  ...          0       0       0       0   

     Deck_D  Deck_E  Deck_F  Deck_G  Deck_T  Deck_U  
0         0       0       0       0       0       1  
1         0       0       0       0       0       0  
2         0       0       0       0       0       1  
3         0       0       0       0       0       0  
4         0       0       0       0       0       1  
..      ...     ...     ...     ...     ...     ...  
884       0       0       0       0       0       1  
885       0       0       0       0       0       0  
886       0       0       0       0       0       1  
887       0       0       0       0       0       0  
888       0       0       0       0       0       1  

[889 rows x 26 columns]

## Select features

In [3]:
# Set features. This will also be used as your x values.
selected_features = df[["Pclass", "Age", "Fare", "Family_Size", "Age*Class", "Fare_Per_Person", "Sex_female", "Title_Mr"]]
feature_names = selected_features.columns

## Create a Train Test Split

In [4]:
# assign X(data) and y(target)
data = selected_features
target = df["Survived"]
print(data.shape, target.shape)

(889, 8) (889,)


In [5]:
# split the data into training and testing
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(data, target, random_state=42)

In [6]:
X_train

Pclass  Age     Fare  Family_Size  Age*Class  Fare_Per_Person  \
375       3   22   7.2500            0         66           7.2500   
457       2   50  10.5000            0        100          10.5000   
731       2   36   0.0000            0         72           0.0000   
506       1   20  26.5500            0         20          26.5500   
828       3   15  14.4542            1         45           7.2271   
..      ...  ...      ...          ...        ...              ...   
106       3   35   7.7750            0        105           7.7750   
270       3   25   0.0000            0         75           0.0000   
860       1   48  25.9292            0         48          25.9292   
435       3   21  34.3750            4         63           6.8750   
102       3   33   8.6542            0         99           8.6542   

     Sex_female  Title_Mr  
375           1         0  
457           1         0  
731           0         1  
506           0         1  
828           1         0  
..          ...       ...  
106           0         1  
270           0         1  
860           1         0  
435           1         0  
102           0         1  

[666 rows x 8 columns]

## Pre-processing

In [7]:
# Scale your data
from sklearn.preprocessing import StandardScaler
X_scaler = StandardScaler().fit(X_train)
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

## Train the model

In [8]:
# create a LinearSVC Model
from sklearn.svm import LinearSVC
model = LinearSVC(random_state=0, tol=1e-5)
model

LinearSVC(random_state=0, tol=1e-05)

In [9]:
# fit(train) our model using the training data
model.fit(X_train_scaled, y_train)

C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py:976: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


LinearSVC(random_state=0, tol=1e-05)

In [10]:
# validate the model using the test data
print(f"Training Data Score: {model.score(X_train_scaled, y_train)}")
print(f"Testing Data Score: {model.score(X_test_scaled, y_test)}")

Training Data Score: 0.8348348348348348
Testing Data Score: 0.7982062780269058


In [11]:
pred_df = pd.DataFrame({"Predictions": model.predict(X_test_scaled), "Actual": y_test})
pred_df

Predictions  Actual
280            0       0
434            1       1
39             1       1
417            0       0
584            1       1
..           ...     ...
424            0       0
101            0       0
199            0       0
398            1       1
668            1       1

[223 rows x 2 columns]

## Hyperparameter Tuning

In [16]:
# Create the GridSearchCV model/estimator along with a parameter object containing the values to adjust
from sklearn.model_selection import GridSearchCV
param_grid = {'random_state': [0, 42],
              'tol': [1, 100, 1000, 10000, 10000, 1000000, 10000000],
              'loss': ['hinge', 'square_hinge'],
              'dual': [True, False],
              'penalty': ['l1', 'l2'],
              'fit_intercept': [True, False],
              'C': [1, 5, 10, 50]}
grid = GridSearchCV(model, param_grid, verbose=3)

In [17]:
# Train the model with GridSearch estimator...
# this will take the model and try each combination of parameters
grid.fit(X_train_scaled, y_train)

Fitting 5 folds for each of 896 candidates, totalling 4480 fits
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l1, random_state=0, tol=1 
[CV]  C=1, dual=True, fit_intercept=True

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_classes.py", line 233, in fit
    self.coef_, self.intercept_, self.n_iter_ = _fit_liblinear(
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 965, in _fit_liblinear
    solver_type = _get_liblinear_solver_type(multi_class, penalty, loss, dual)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 821, in _get_liblinear_solver_type
    raise ValueError('Unsupported set of arg


[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=1 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=1, score=0.835, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100, score=0.739, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100, score=0.805, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100, score=0.797, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random_state=42, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=hinge, penalty=l2, random

C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_classes.py", line 233, in fit
    self.coef_, self.intercept_, self.n_iter_ = _fit_liblinear(
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 965, in _fit_liblinear
    solver_type = _get_liblinear_solver_type(multi_class, penalty, loss, dual)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 821, in _get_liblinear_solver_type
    raise ValueError('Unsupported set of arguments: %s, '
ValueError: Unsupported set of arguments: loss='square_hinge' is no

[CV]  C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100 
[CV]  C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=100, score=nan, total=   0.0s
[CV] C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=1000 
[CV]  C=1, dual=True, fit_intercept=True, loss=square_hinge, penalty=l2, random_state=0, tol=1000, score=nan, total=   

...


[CV] C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000 
[CV]  C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000 
[CV]  C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000 
[CV]  C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000 
[CV]  C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=hinge, penalty=l1, random_state=42, tol=1000000 
[CV]  C=50, d

C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_classes.py", line 233, in fit
    self.coef_, self.intercept_, self.n_iter_ = _fit_liblinear(
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 965, in _fit_liblinear
    solver_type = _get_liblinear_solver_type(multi_class, penalty, loss, dual)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 821, in _get_liblinear_solver_type
    raise ValueError('Unsupported set of arguments: %s, '
ValueError: Unsupported set of arguments: The combination of penalt

[CV]  C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1 
[CV]  C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1 
[CV]  C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=100 
[CV]  C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=100, score=nan, total=   0.0s
[CV] C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=100 
[CV]  C=50, dual=False, fit_intercept=False, loss=square_hinge, penalty=l1, random_state=42, tol=1

C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_classes.py", line 233, in fit
    self.coef_, self.intercept_, self.n_iter_ = _fit_liblinear(
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 965, in _fit_liblinear
    solver_type = _get_liblinear_solver_type(multi_class, penalty, loss, dual)
  File "C:\Users\stuhu\anaconda3\lib\site-packages\sklearn\svm\_base.py", line 821, in _get_liblinear_solver_type
    raise ValueError('Unsupported set of arguments: %s, '
ValueError: Unsupported set of arguments: loss='square_hinge' is no

GridSearchCV(estimator=LinearSVC(random_state=0, tol=1e-05),
             param_grid={'C': [1, 5, 10, 50], 'dual': [True, False],
                         'fit_intercept': [True, False],
                         'loss': ['hinge', 'square_hinge'],
                         'penalty': ['l1', 'l2'], 'random_state': [0, 42],
                         'tol': [1, 100, 1000, 10000, 10000, 1000000,
                                 10000000]},
             verbose=3)

In [18]:
# list the best parameters for this dataset, then list the best score
print(grid.best_params_)
print(grid.best_score_)

{'C': 1, 'dual': True, 'fit_intercept': True, 'loss': 'hinge', 'penalty': 'l2', 'random_state': 0, 'tol': 1}
0.8393446302322971


In [19]:
# make predictions with the hypertuned model
predictions = grid.predict(X_test_scaled)

In [20]:
grid_df = pd.DataFrame({"Predictions": predictions, "Actual": y_test})
grid_df

Predictions  Actual
280            0       0
434            1       1
39             1       1
417            0       0
584            1       1
..           ...     ...
424            0       0
101            0       0
199            0       0
398            1       1
668            1       1

[223 rows x 2 columns]

In [21]:
# calculate classification report
# precision = true positive / (true positive + false positive)
# recall = true positive / (true positive + false negative)
# f1 = 2*((precision * recall) / (precision + recall)): best at 1, worst at 0
from sklearn.metrics import classification_report
print(classification_report(y_test, predictions))

              precision    recall  f1-score   support

           0       0.85      0.84      0.84       141
           1       0.73      0.74      0.73        82

    accuracy                           0.80       223
   macro avg       0.79      0.79      0.79       223
weighted avg       0.80      0.80      0.80       223



## Test the model

In [22]:
# loading the dataset
test_data = pd.read_csv("resources/test_transformed_2.csv")
test_data

PassengerId  Pclass  Age  SibSp  Parch      Fare  Family_Size  Age*Class  \
0            892       3   34      0      0    7.8292            0        102   
1            893       3   47      1      0    7.0000            1        141   
2            894       2   62      0      0    9.6875            0        124   
3            895       3   27      0      0    8.6625            0         81   
4            896       3   22      1      1   12.2875            2         66   
..           ...     ...  ...    ...    ...       ...          ...        ...   
413         1305       3   42      0      0    8.0500            0        126   
414         1306       1   39      0      0  108.9000            0         39   
415         1307       3   38      0      0    7.2500            0        114   
416         1308       3   27      0      0    8.0500            0         81   
417         1309       3   25      1      1   22.3583            2         75   

     Fare_Per_Person  Sex_female  ...  Title_Mr  Title_Mrs  Deck_A  Deck_B  \
0           7.829200           0  ...         1          0       0       0   
1           3.500000           1  ...         0          1       0       0   
2           9.687500           0  ...         1          0       0       0   
3           8.662500           0  ...         1          0       0       0   
4           4.095833           1  ...         0          1       0       0   
..               ...         ...  ...       ...        ...     ...     ...   
413         8.050000           0  ...         1          0       0       0   
414       108.900000           1  ...         1          0       0       0   
415         7.250000           0  ...         1          0       0       0   
416         8.050000           0  ...         1          0       0       0   
417         7.452767           0  ...         0          0       0       0   

     Deck_C  Deck_D  Deck_E  Deck_F  Deck_G  Deck_U  
0         0       0       0       0       0       1  
1         0       0       0       0       0       1  
2         0       0       0       0       0       1  
3         0       0       0       0       0       1  
4         0       0       0       0       0       1  
..      ...     ...     ...     ...     ...     ...  
413       0       0       0       0       0       1  
414       1       0       0       0       0       0  
415       0       0       0       0       0       1  
416       0       0       0       0       0       1  
417       0       0       0       0       0       1  

[418 rows x 25 columns]

In [23]:
# save the model if evaluation is promising
import joblib
filename = 'models/linearSVC.sav'
joblib.dump(grid, filename)

['models/linearSVC.sav']

In [24]:
# create variables for training and testing data
X_train = df[["Pclass", "Age", "Fare", "Family_Size", "Age*Class", "Fare_Per_Person", "Sex_female", "Title_Mr"]]
y_train = df["Survived"]

X_test = test_data[["Pclass", "Age", "Fare", "Family_Size", "Age*Class", "Fare_Per_Person", "Sex_female", "Title_Mr"]]

In [25]:
# Scale your data
from sklearn.preprocessing import StandardScaler
X_scaler = StandardScaler().fit(X_train)
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [26]:
# create a Linear SVC Model with new parameters
model = LinearSVC(C=1, dual=True, fit_intercept=True, loss='hinge', penalty='l2', random_state=42, tol=1)
model

LinearSVC(C=1, loss='hinge', random_state=42, tol=1)

In [27]:
# fit(train) our model using the training data
model.fit(X_train_scaled, y_train)

LinearSVC(C=1, loss='hinge', random_state=42, tol=1)

In [28]:
# make predictions with the hypertuned model
predictions = model.predict(X_test_scaled)

In [29]:
output = pd.DataFrame({'PassengerID': test_data.PassengerId, 'Survived': predictions})

In [30]:
# submission using grid hyperparameter tuned model
output.to_csv('submissions/Hunter_submission10.csv', index=False)